In [10]:
# Install with pip install firecrawl-py
from firecrawl import FirecrawlApp

app = FirecrawlApp(api_key='fc-1c53f74c1f2e42948a9ec51366d90969')

crawl_result = app.crawl_url('https://www.timreview.ca/', params={
'limit': 10,
'maxDepth': 2,
'includePaths': [ 'article/*' ],
'scrapeOptions': {
	'formats': [ 'markdown' ],
  }
})

In [11]:
crawl_result

{'success': True,
 'status': 'completed',
 'completed': 1,
 'total': 1,
 'creditsUsed': 1,
 'expiresAt': '2025-01-27T02:11:17.000Z',
 'data': [{'markdown': '[Skip to main content](https://www.timreview.ca/#main-content)\n\nThe\xa0_Technology Innovation Management Review_ (TIM Review)\xa0provides insightful content about the issues and emerging trends\xa0relevant to launching and growing technology businesses. The TIM Review focuses on the theories, strategies, and tools that help small and large technology companies succeed.\n\nOur readers are looking for practical ideas they can apply within their own organizations. The TIM Review brings together diverse viewpoints - from academics, entrepreneurs, companies of all sizes, the public sector, the community sector, and others - to bridge the gap between theory and practice, with a particular focus on the topics of technology and global entrepreneurship in small and large companies.\n\n### Latest Issue\n\n![](https://www.timreview.ca/sites

In [6]:
from IPython.core.display import HTML, display

/var/folders/xk/srqz8jbj0dsg2b_nsfgjn1lh0000gn/T/ipykernel_25541/489027457.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython.display
  from IPython.core.display import HTML, display


In [7]:
display(HTML(response['html']))

In [14]:
import os
import requests
from bs4 import BeautifulSoup
from urllib.parse import urlparse, urljoin

def download_pdfs_from_domain(start_url, domain, download_folder="downloaded_pdfs"):
    """
    Scrapes and downloads all PDF files from the specified domain.

    Parameters:
    - start_url (str): The starting URL to begin scraping.
    - domain (str): The domain to restrict crawling to (e.g., 'timreview.ca').
    - download_folder (str): The folder to save downloaded PDFs.
    """
    # Create the folder if it doesn't exist
    if not os.path.exists(download_folder):
        os.makedirs(download_folder)

    # Keep track of visited URLs to avoid reprocessing
    visited = set()

    def crawl_page(url):
        """Crawls a single page for PDF links and internal URLs."""
        if url in visited:
            return  # Skip already visited URLs
        visited.add(url)

        try:
            # Fetch the webpage content
            response = requests.get(url)
            response.raise_for_status()

            # Parse the HTML with BeautifulSoup
            soup = BeautifulSoup(response.text, 'html.parser')

            # Find all links in the page
            for link in soup.find_all('a', href=True):
                href = link['href']

                # Resolve relative URLs
                full_url = urljoin(url, href)

                # Check if the link belongs to the same domain
                if domain in urlparse(full_url).netloc:
                    # If it's a PDF, download it
                    if full_url.endswith('.pdf'):
                        download_pdf(full_url)
                    # Otherwise, continue crawling
                    elif full_url not in visited:
                        crawl_page(full_url)

        except Exception as e:
            print(f"Error crawling {url}: {e}")

    def download_pdf(pdf_url):
        """Downloads a PDF file."""
        try:
            file_name = os.path.join(download_folder, os.path.basename(pdf_url))
            print(f"Downloading: {pdf_url}")
            pdf_response = requests.get(pdf_url)
            pdf_response.raise_for_status()

            with open(file_name, 'wb') as pdf_file:
                pdf_file.write(pdf_response.content)
            print(f"Saved to: {file_name}")
        except Exception as e:
            print(f"Error downloading {pdf_url}: {e}")

    # Start crawling from the initial URL
    crawl_page(start_url)

# Example Usage
start_page = "https://www.timreview.ca/"  # Replace with the starting page URL
domain = "timreview.ca"  # Restrict to this domain
download_pdfs_from_domain(start_page, domain)

Error crawling https://timreview.ca/topic/SERS_Project: HTTPSConnectionPool(host='globalsers.org', port=443): Max retries exceeded with url: / (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x30b650bd0>, 'Connection to globalsers.org timed out. (connect timeout=None)'))
Downloading: https://timreview.ca/sites/default/files/Issue_PDF/TIMReview_February2013.pdf
Saved to: downloaded_pdfs/TIMReview_February2013.pdf
Downloading: https://timreview.ca/sites/default/files/Issue_PDF/august07_osbr.pdf
Saved to: downloaded_pdfs/august07_osbr.pdf
Downloading: https://timreview.ca/sites/default/files/Issue_PDF/TIMReview_2022_Issue_1-2-cover.pdf
Saved to: downloaded_pdfs/TIMReview_2022_Issue_1-2-cover.pdf
Error crawling https://timreview.ca/user/100/article: 403 Client Error: Forbidden for url: https://timreview.ca/user/100/article
Downloading: https://timreview.ca/sites/default/files/Issue_PDF/january08_osbr.pdf
Saved to: downloaded_pdfs/january08_osbr.pdf
Downloading:

KeyboardInterrupt: 

In [15]:
import requests
from bs4 import BeautifulSoup
import re

def get_pdf_links(domain_url):
    try:
        # Fetch the website content
        response = requests.get(domain_url)
        response.raise_for_status()  # Raise an error for bad responses
        
        # Parse the website content
        soup = BeautifulSoup(response.text, 'html.parser')
        
        # Find all anchor tags
        links = soup.find_all('a', href=True)
        
        # Filter for PDF links
        pdf_links = [link['href'] for link in links if link['href'].endswith('.pdf')]
        
        # Make relative URLs absolute
        pdf_links = [requests.compat.urljoin(domain_url, link) for link in pdf_links]
        
        return pdf_links
    except requests.exceptions.RequestException as e:
        print(f"Error fetching the domain: {e}")
        return []

# Example usage
domain = "https://timreview.ca"
pdf_links = get_pdf_links(domain)

if pdf_links:
    print("PDF Links found:")
    for pdf in pdf_links:
        print(pdf)
else:
    print("No PDF links found.")

PDF Links found:
https://timreview.ca/sites/default/files/Issue_PDF/TIMReview_2022_Issue_1-2-cover.pdf


In [31]:
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin, urlparse, urldefrag
import re
from collections import deque

# Parameters
domain = "https://timreview.ca"
start_url = domain
max_depth = 10

# Data structures
visited = set()
article_links = set()
queue = deque([(start_url, 0)])  # (URL, current depth)

# Helper function to extract and validate links
def extract_links(url):
    try:
        response = requests.get(url, timeout=10)
        if response.status_code != 200:
            return []
        soup = BeautifulSoup(response.text, 'html.parser')
        links = set()
        for a_tag in soup.find_all('a', href=True):
            href = urljoin(url, a_tag['href'])  # Convert relative to absolute URL
            href, _ = urldefrag(href)  # Remove fragment (#tag) from the URL
            if is_valid_link(href):
                links.add(href)
        return links
    except Exception as e:
        print(f"Error fetching {url}: {e}")
        return []

# Helper function to check if a link is valid
def is_valid_link(link):
    parsed = urlparse(link)
    return (
        parsed.netloc == "timreview.ca" and  # Ensure the domain matches
        re.search(r'/article/\d+', parsed.path)  # Match the article pattern
    )

# Main crawling loop
while queue:
    current_url, depth = queue.popleft()
    if depth > max_depth or current_url in visited:
        continue

    visited.add(current_url)
    links = extract_links(current_url)
    
    for link in links:
        if link not in visited and link not in article_links:
            if re.search(r'/article/\d+', urlparse(link).path):  # Check for article pattern
                article_links.add(link)
                print(f"Found {len(article_links)}: {link}")
            queue.append((link, depth + 1))

Found 1: https://timreview.ca/article/1477
Found 2: https://timreview.ca/article/1478
Found 3: https://timreview.ca/article/1479
Found 4: https://timreview.ca/article/1482
Found 5: https://timreview.ca/article/1481
Found 6: https://timreview.ca/article/1483
Found 7: https://timreview.ca/article/1480
Found 8: https://timreview.ca/article/1450
Found 9: https://timreview.ca/article/1445
Found 10: https://timreview.ca/article/1447
Found 11: https://timreview.ca/article/1449
Found 12: https://timreview.ca/article/1209
Found 13: https://timreview.ca/article/1111
Found 14: https://timreview.ca/article/1446
Found 15: https://timreview.ca/article/1291
Found 16: https://timreview.ca/article/1108
Found 17: https://timreview.ca/article/1422
Found 18: https://timreview.ca/article/1368
Found 19: https://timreview.ca/article/1407
Found 20: https://timreview.ca/article/1444
Found 21: https://timreview.ca/article/1448
Found 22: https://timreview.ca/article/1112
Found 23: https://timreview.ca/article/88

In [40]:
len(article_links)

1601

In [59]:
import json

with open('filtered_pdf_links.json', "w") as f:
    json.dump(list(filtered_pdf_urls), f, indent=4)
    print(f"Saved {len(filtered_pdf_urls)} article links to {'filtered_pdf_links.json'}")

Saved 768 article links to filtered_pdf_links.json


In [42]:
len(links)

40

In [44]:
import re


# Regex pattern to match the valid format
pattern = r"^https://timreview\.ca/article/\d+$"

# Filter the list
filtered_urls = [url for url in article_links if re.match(pattern, url)]

print(filtered_urls)

['https://timreview.ca/article/1435', 'https://timreview.ca/article/1313', 'https://timreview.ca/article/1268', 'https://timreview.ca/article/211', 'https://timreview.ca/article/911', 'https://timreview.ca/article/130', 'https://timreview.ca/article/1129', 'https://timreview.ca/article/1253', 'https://timreview.ca/article/674', 'https://timreview.ca/article/300', 'https://timreview.ca/article/287', 'https://timreview.ca/article/242', 'https://timreview.ca/article/549', 'https://timreview.ca/article/272', 'https://timreview.ca/article/200', 'https://timreview.ca/article/249', 'https://timreview.ca/article/199', 'https://timreview.ca/article/1002', 'https://timreview.ca/article/524', 'https://timreview.ca/article/369', 'https://timreview.ca/article/1142', 'https://timreview.ca/article/1099', 'https://timreview.ca/article/288', 'https://timreview.ca/article/793', 'https://timreview.ca/article/811', 'https://timreview.ca/article/121', 'https://timreview.ca/article/277', 'https://timreview.

In [46]:
len(filtered_urls)

1118

In [52]:
pdf_links = []

# Check each URL for a PDF link
for url in filtered_urls:
    try:
        response = requests.get(url)
        response.raise_for_status()  # Raise an error if the request failed
        soup = BeautifulSoup(response.text, 'html.parser')
        # Find all links ending with .pdf
        pdf_link = soup.find('a', href=lambda href: href and href.endswith('.pdf'))
        if pdf_link:
            pdf_links.append(pdf_link['href'])  # Add PDF link to the list
            print(f'Found PDF link: {pdf_link["href"]}')
    except Exception as e:
        print(f"Error processing {url}: {e}")

print("PDF Links:", pdf_links)

Found PDF link: https://timreview.ca/sites/default/files/article_PDF/TIMReview_2021_April%20-%204.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/TIMReview_January2020%20-%20D.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/TIMReview_September2019%20-%20final-E.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/Capdevila_et_al_TIMReview_July2015.pdf
Found PDF link: http://www.e-cology.ca/canfloss/report/CANfloss_Report.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/Joshi_TIMReview_January2018.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/Khademi_TIMReview_July2019.pdf
Found PDF link: https://timreview.ca/sites/default/files/article_PDF/SolesvikGulbrandsen_TIMReview_April2013.pdf
Found PDF link: http://www.rpi.edu/~nambis/nambisan_amr.pdf
Found PDF link: http://cyber.law.harvard.edu/interop/pdfs/interop-mashups.pdf
Found PDF link: https://timreview.ca/sites/defaul

In [54]:
len(pdf_links)

892

In [56]:
import re



# Regex pattern to match only URLs from the timreview.ca domain
pattern = r"^https?://timreview\.ca/.*"

# Filter URLs
filtered_pdf_urls = [url for url in pdf_links if re.match(pattern, url)]

print("Filtered URLs:", filtered_pdf_urls)

Filtered URLs: ['https://timreview.ca/sites/default/files/article_PDF/TIMReview_2021_April%20-%204.pdf', 'https://timreview.ca/sites/default/files/article_PDF/TIMReview_January2020%20-%20D.pdf', 'https://timreview.ca/sites/default/files/article_PDF/TIMReview_September2019%20-%20final-E.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Capdevila_et_al_TIMReview_July2015.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Joshi_TIMReview_January2018.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Khademi_TIMReview_July2019.pdf', 'https://timreview.ca/sites/default/files/article_PDF/SolesvikGulbrandsen_TIMReview_April2013.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Wells_TIMReview_April2012.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Kage_et_al_TIMReview_July2016.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Zhou_TIMReview_February2012.pdf', 'https://timreview.ca/sites/default/files/article_PDF/Ik%C3%A4valko_et_al

In [58]:
len(filtered_pdf_urls)

768

In [ ]:
import requests
from bs4 import BeautifulSoup
import os

# List of URLs to check for PDFs
urls = [
    "https://timreview.ca/article/355",
    "https://timreview.ca/article/356",
    "https://timreview.ca/article/358",
    "https://timreview.ca/article/360",
]

# Directory to save downloaded PDFs
download_dir = "pdf_downloads"
os.makedirs(download_dir, exist_ok=True)  # Create directory if it doesn't exist

def download_pdf(pdf_url, save_path):
    """Download a PDF from a URL and save it to the specified path."""
    try:
        response = requests.get(pdf_url, stream=True)
        response.raise_for_status()
        with open(save_path, 'wb') as f:
            for chunk in response.iter_content(chunk_size=8192):
                f.write(chunk)
        print(f"Downloaded: {save_path}")
    except Exception as e:
        print(f"Failed to download {pdf_url}: {e}")

# Find and download PDFs
for idx, url in enumerate(urls, start=1):
    try:
        response = requests.get(url)
        response.raise_for_status()
        soup = BeautifulSoup(response.text, 'html.parser')
        pdf_link = soup.find('a', href=lambda href: href and href.endswith('.pdf'))
        if pdf_link:
            pdf_url = pdf_link['href']
            if not pdf_url.startswith('http'):
                pdf_url = f"https://timreview.ca{pdf_url}"  # Handle relative links
            pdf_filename = os.path.join(download_dir, os.path.basename(pdf_url))
            print(f"({idx}/{len(urls)}) Found PDF: {pdf_url}")
            download_pdf(pdf_url, pdf_filename)
        else:
            print(f"({idx}/{len(urls)}) No PDF found on {url}")
    except Exception as e:
        print(f"({idx}/{len(urls)}) Failed to process {url}: {e}")

In [ ]:
import os
import requests
from tqdm import tqdm

# Create a folder to store the PDFs
output_folder = "downloaded_pdfs"
os.makedirs(output_folder, exist_ok=True)


# Download each PDF with progress bar
for index, url in enumerate(filtered_pdf_urls):
    try:
        # Send a GET request
        response = requests.get(url, stream=True)
        response.raise_for_status()  # Raise an error for bad responses (4xx and 5xx)

        # Get the file size from the headers
        file_size = int(response.headers.get('Content-Length', 0))

        # Extract the filename from the URL
        filename = os.path.basename(url.split("?")[0])  # Remove query parameters if any
        if not filename.endswith(".pdf"):
            filename = f"file_{index + 1}.pdf"

        # Path to save the file
        filepath = os.path.join(output_folder, filename)

        # Download the file with a progress bar
        with open(filepath, "wb") as file, tqdm(
            desc=f"Downloading {filename}",
            total=file_size,
            unit="B",
            unit_scale=True,
            unit_divisor=1024,
        ) as bar:
            for chunk in response.iter_content(chunk_size=1024):
                file.write(chunk)
                bar.update(len(chunk))

        print(f"Downloaded: {filename}")
    except requests.exceptions.RequestException as e:
        print(f"Failed to download {url}: {e}")

print("All downloads completed!")

In [62]:
import pandas as pd

# List of URLs

# Extract the article number and create a list of dictionaries
data = [{"number": int(url.split("/")[-1]), "url": url} for url in filtered_urls]

# Create a DataFrame
df = pd.DataFrame(data)

print(df)

      number                                url
0       1435  https://timreview.ca/article/1435
1       1313  https://timreview.ca/article/1313
2       1268  https://timreview.ca/article/1268
3        211   https://timreview.ca/article/211
4        911   https://timreview.ca/article/911
...      ...                                ...
1113    1169  https://timreview.ca/article/1169
1114     111   https://timreview.ca/article/111
1115     769   https://timreview.ca/article/769
1116     673   https://timreview.ca/article/673
1117    1329  https://timreview.ca/article/1329

[1118 rows x 2 columns]


In [63]:
article_metadata = df

In [64]:
article_metadata.to_csv('article_metadata.csv', index=False)

In [65]:
article_metadata

number                                url
0       1435  https://timreview.ca/article/1435
1       1313  https://timreview.ca/article/1313
2       1268  https://timreview.ca/article/1268
3        211   https://timreview.ca/article/211
4        911   https://timreview.ca/article/911
...      ...                                ...
1113    1169  https://timreview.ca/article/1169
1114     111   https://timreview.ca/article/111
1115     769   https://timreview.ca/article/769
1116     673   https://timreview.ca/article/673
1117    1329  https://timreview.ca/article/1329

[1118 rows x 2 columns]

In [66]:
article_metadata = article_metadata.sort_values(by='number')

In [67]:
article_metadata

number                                url
898       53    https://timreview.ca/article/53
241       54    https://timreview.ca/article/54
368       55    https://timreview.ca/article/55
1011      56    https://timreview.ca/article/56
1013      57    https://timreview.ca/article/57
...      ...                                ...
635     1479  https://timreview.ca/article/1479
345     1480  https://timreview.ca/article/1480
291     1481  https://timreview.ca/article/1481
631     1482  https://timreview.ca/article/1482
759     1483  https://timreview.ca/article/1483

[1118 rows x 2 columns]

In [73]:
df = article_metadata.copy()

In [ ]:
import pandas as pd
import requests
from bs4 import BeautifulSoup


# Function to extract PDF and BibTeX URLs
def extract_file_urls(url):
    try:
        response = requests.get(url, timeout=10)
        response.raise_for_status()
        soup = BeautifulSoup(response.text, "html.parser")
        
        pdf_url = None
        bibtex_url = None
        
        # Check for links with ".pdf" and "bibtex"
        for link in soup.find_all("a", href=True):
            href = link["href"]
            if "timreview.ca" in href and href.endswith(".pdf"):
                pdf_url = href
            if "bibtex" in href:
                bibtex_url = href
                
        return pdf_url, bibtex_url
    except requests.RequestException as e:
        print(f"Error accessing {url}: {e}")
        return None, None

# Populate the DataFrame with PDF and BibTeX URLs
df["pdf_url"] = None
df["bibtex_url"] = None

for idx, row in tqdm(df.iterrows()):
    pdf_url, bibtex_url = extract_file_urls(row["url"])
    df.at[idx, "pdf_url"] = pdf_url
    df.at[idx, "bibtex_url"] = bibtex_url

# Print or save the final DataFrame
print(df)

In [79]:
df['bibtex_url'] = df['bibtex_url'].apply(
    lambda x: f"https://timreview.ca{x}" if pd.notnull(x) and not x.startswith("https://timreview.ca") else x
)

In [80]:
df

number                                url  \
898       53    https://timreview.ca/article/53   
241       54    https://timreview.ca/article/54   
368       55    https://timreview.ca/article/55   
1011      56    https://timreview.ca/article/56   
1013      57    https://timreview.ca/article/57   
...      ...                                ...   
635     1479  https://timreview.ca/article/1479   
345     1480  https://timreview.ca/article/1480   
291     1481  https://timreview.ca/article/1481   
631     1482  https://timreview.ca/article/1482   
759     1483  https://timreview.ca/article/1483   

                                                pdf_url  \
898                                                None   
241                                                None   
368                                                None   
1011                                               None   
1013                                               None   
...                                                 ...   
635   https://timreview.ca/sites/default/files/artic...   
345   https://timreview.ca/sites/default/files/artic...   
291   https://timreview.ca/sites/default/files/artic...   
631   https://timreview.ca/sites/default/files/artic...   
759   https://timreview.ca/sites/default/files/artic...   

                                           bibtex_url  
898     https://timreview.ca/article/export/bibtex/53  
241     https://timreview.ca/article/export/bibtex/54  
368     https://timreview.ca/article/export/bibtex/55  
1011    https://timreview.ca/article/export/bibtex/56  
1013    https://timreview.ca/article/export/bibtex/57  
...                                               ...  
635   https://timreview.ca/article/export/bibtex/1479  
345   https://timreview.ca/article/export/bibtex/1480  
291   https://timreview.ca/article/export/bibtex/1481  
631   https://timreview.ca/article/export/bibtex/1482  
759   https://timreview.ca/article/export/bibtex/1483  

[1118 rows x 4 columns]

In [ ]:
# Create the directory if it doesn't exist
os.makedirs("bibtex", exist_ok=True)

# Download BibTeX files
for idx, row in tqdm(df.iterrows()):
    bibtex_url = row['bibtex_url']
    number = row['number']
    
    if pd.notnull(bibtex_url):  # Ensure the URL is not null
        try:
            response = requests.get(bibtex_url, timeout=10)
            response.raise_for_status()  # Raise an error for unsuccessful status codes
            
            # Save the content to a file named <number>.bib
            file_path = os.path.join("bibtex", f"{number}.bib")
            with open(file_path, "w", encoding="utf-8") as file:
                file.write(response.text)
            
            print(f"Downloaded: {file_path}")
        except requests.RequestException as e:
            print(f"Failed to download {bibtex_url}: {e}")

print("All downloads completed.")

In [95]:
article_metadata = df.copy()

In [97]:
article_metadata.to_csv('article_metadata.csv', index=False)

In [90]:
df = article_metadata.copy()

In [91]:
import os
import pandas as pd
from bibtexparser.bparser import BibTexParser
from bibtexparser.customization import convert_to_unicode


# Directory containing the BibTeX files
bibtex_dir = "bibtex"

# Function to parse a BibTeX file and extract its entries
def parse_bibtex(file_path):
    try:
        with open(file_path, "r", encoding="utf-8") as bib_file:
            parser = BibTexParser()
            parser.customization = convert_to_unicode
            bib_database = parser.parse_file(bib_file)
            return bib_database.entries[0] if bib_database.entries else {}
    except Exception as e:
        print(f"Error parsing BibTeX file {file_path}: {e}")
        return {}

# Iterate through the DataFrame and populate columns based on BibTeX content
for idx, row in tqdm(df.iterrows()):
    number = row["number"]
    bibtex_file = os.path.join(bibtex_dir, f"{number}.bib")
    
    if os.path.exists(bibtex_file):  # Check if the file exists
        bibtex_data = parse_bibtex(bibtex_file)
        for key, value in bibtex_data.items():
            # Add the key as a new column if it doesn't exist, and populate it
            if key not in df.columns:
                df[key] = None
            df.at[idx, key] = value

1118it [00:04, 224.40it/s]


In [93]:
df.columns = df.columns.str.lower()

In [94]:
df

number                             url  \
0         53  http://timreview.ca/article/53   
1         54  http://timreview.ca/article/54   
2         55  http://timreview.ca/article/55   
3         56  http://timreview.ca/article/56   
4         57  http://timreview.ca/article/57   
...      ...                             ...   
1113    1479       timreview.ca/article/1479   
1114    1480       timreview.ca/article/1480   
1115    1481       timreview.ca/article/1481   
1116    1482       timreview.ca/article/1482   
1117    1483       timreview.ca/article/1483   

                                                pdf_url  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
1113  https://timreview.ca/sites/default/files/artic...   
1114  https://timreview.ca/sites/default/files/artic...   
1115  https://timreview.ca/sites/default/files/artic...   
1116  https://timreview.ca/sites/default/files/artic...   
1117  https://timreview.ca/sites/default/files/artic...   

                                           bibtex_url  \
0       https://timreview.ca/article/export/bibtex/53   
1       https://timreview.ca/article/export/bibtex/54   
2       https://timreview.ca/article/export/bibtex/55   
3       https://timreview.ca/article/export/bibtex/56   
4       https://timreview.ca/article/export/bibtex/57   
...                                               ...   
1113  https://timreview.ca/article/export/bibtex/1479   
1114  https://timreview.ca/article/export/bibtex/1480   
1115  https://timreview.ca/article/export/bibtex/1481   
1116  https://timreview.ca/article/export/bibtex/1482   
1117  https://timreview.ca/article/export/bibtex/1483   

                                                 author       issn  \
0                                           Dru Lavigne  1913-6102   
1                                         Stormy Peters  1913-6102   
2                                            Sourcelabs  1913-6102   
3                       Jason Côté and Julian Egelstaff  1913-6102   
4                                          Glen McInnis  1913-6102   
...                                                 ...        ...   
1113  Abu Naser Mohammad Saif and K. M. Anwarul Isla...  1927-0321   
1114                                    Marc Pilkington  1927-0321   
1115                   Anitha Kumari and N. Chitra Devi  1927-0321   
1116  Maryanne Morrow and Matthew Midson and Gregory...  1927-0321   
1117  Maryanne Morrow and Matthew Midson and Gregory...  1927-0321   

                                               abstract address       type  \
0     What is your first thought when you encounter ...  Ottawa  Editorial   
1     Open Source Software (OSS) has permeated the e...  Ottawa   Articles   
2     Infrastructure Open Source Software (OSS), inc...  Ottawa   Articles   
3     In 2004, the Nonprofit Open Source Initiative ...  Ottawa   Articles   
4     Early in 2006, Microsoft CEO Steve Balmer made...  Ottawa   Articles   
...                                                 ...     ...        ...   
1113  Contemporary research on technology and innova...  Ottawa       None   
1114  The paper sets out to examine the relevance of...  Ottawa       None   
1115  With the emergence of new technologies, banks ...  Ottawa       None   
1116  This interview on “Blockchain and Digital Tran...  Ottawa       None   
1117  This interview on “Blockchain and Digital Tran...  Ottawa       None   

                 publisher  ...  year  \
0     Talent First Network  ...  2007   
1     Talent First Network  ...  2007   
2     Talent First Network  ...  2007   
3     Talent First Network  ...  2007   
4     Talent First Network  ...  2007   
...        